In [1]:
import pandas as pd
import scipy.sparse as sparse
import numpy as np
from scipy.sparse.linalg import spsolve

try:
    import implicit
except Exception:
    !pip install implicit
    import implicit

In [2]:
vertical = 'b'

In [3]:
def data_vert():# Полуаем dataframe с соответствующимим коэффициентами для пар взаимодействий user-item
    data1 = pd.read_csv('converted_users_' + vertical + '.csv')
    data2 = pd.read_csv('interested_users_' + vertical + '.csv')
    
    data2['Quantity'] = np.ones(data2.shape[0]) * 0.01
    data1['Quantity'] = np.ones(data1.shape[0]) * 0.1
    data1.loc[data1['action_type'].isin([0, 3, 4]), 'Quantity'] = 1
    data1 = data1.append(data2[data2.user_id.isin(set(data1.user_id))], ignore_index=True)
    
#     gb = pd.DataFrame({'cnt': data1.groupby('user_id').product_id.nunique()})
    gb = pd.DataFrame({'cnt': data1[data1.action_type.isin([0, 3, 4])].groupby('user_id').product_id.nunique()})
    indexes = set(gb[gb.cnt >= 2].index)
    
    return data1[data1.user_id.isin(indexes)]

In [4]:
retail_data = data_vert()
retail_data.head()
len(retail_data.user_id.unique())

3470

In [5]:
def get_encoders(data): # возвращает словари чтобы проиндексировать id-шки и поменять их
    uid = dict(enumerate(data.user_id.unique())) #index to id
    uidx = dict([(i[1], i[0]) for i in uid.items()])
    pid = dict(enumerate(data.product_id.unique())) #index to id
    pidx = dict([(i[1], i[0]) for i in pid.items()])
    
    return uid, uidx, pid, pidx

In [6]:
uid, uidx, pid, pidx = get_encoders(retail_data)

In [7]:
len(pid)

74

In [8]:
def get_only_one_purchase(retail_data): # возвращает датафрейм с уникальными покупками для каждого юзера
    data1 = pd.read_csv('converted_users_' + vertical + '.csv')
    
    data1 = data1[data1.action_type.isin([0, 3, 4])]
    data1 = data1[data1.user_id.isin(set(retail_data.user_id))]

    data1['Quantity'] = np.ones(data1.shape[0])
    
    data1 = data1.groupby(['user_id', 'product_id']).max().reset_index()

    return data1

In [9]:
only_one_purchase = get_only_one_purchase(retail_data)
only_one_purchase.head()

user_id  product_id  \
0  0011d2c7700620cb3ff63b2d9ef747e3c55050b9        1288   
1  0011d2c7700620cb3ff63b2d9ef747e3c55050b9        1391   
2  0037b45303116c52c0bef1084e88569d2796a52b        1288   
3  0037b45303116c52c0bef1084e88569d2796a52b        1391   
4  003a6a024d6dc68609c8b0601d24cb23e8694aca          32   

                    date  action_type  Quantity  
0  2021-05-14 10:13:17.0            3       1.0  
1  2021-04-06 11:55:20.0            3       1.0  
2  2021-05-10 12:52:02.0            3       1.0  
3  2021-06-05 13:28:22.0            3       1.0  
4  2021-01-19 17:55:27.0            0       1.0

In [10]:
# меняем id на индексы
retail_data.user_id = retail_data.user_id.apply(lambda x : uidx[x])
retail_data.product_id = retail_data.product_id.apply(lambda x : pidx[x])

only_one_purchase.user_id = only_one_purchase.user_id.apply(lambda x : uidx[x])
only_one_purchase.product_id = only_one_purchase.product_id.apply(lambda x : pidx[x])

In [11]:
def get_sparse_matrix(cleaned_retail, mshape): # возвращает разреженную матрицу для данного dataframe 
    cleaned_retail = cleaned_retail[['product_id', 'Quantity', 'user_id']] # Get rid of unnecessary info
    grouped_cleaned = cleaned_retail.groupby(['user_id', 'product_id']).sum().reset_index() # Group together
#     print(grouped_cleaned[grouped_cleaned.Quantity == grouped_cleaned.Quantity.max()])
    if (grouped_cleaned[grouped_cleaned.Quantity <= 0].shape[0] > 0):
        print("OUPS... :/")
        grouped_cleaned.Quantity.loc[grouped_cleaned.Quantity == 0] = 1 # Replace a sum of zero purchases with a one to
        # indicate purchased
    grouped_purchased = grouped_cleaned.query('Quantity > 0') # Only get customers where purchase totals were positive
    
    customers = list(np.sort(grouped_purchased.user_id.unique())) # Get our unique customers
    products = list(grouped_purchased.product_id.unique()) # Get our unique products that were purchased
    quantity = list(grouped_purchased.Quantity) # All of our purchases

    # rows = grouped_purchased.user_id.astype('category', categories = customers).cat.codes
#     rows = grouped_purchased.user_id.astype('category').cat.codes
    rows = grouped_purchased.user_id
    # Get the associated row indices
#     cols = grouped_purchased.product_id.astype('category').cat.codes 
    cols = grouped_purchased.product_id
    # Get the associated column indices
    purchases_sparse = sparse.csr_matrix((quantity, (rows, cols)), shape=mshape)
    
    matrix_size = purchases_sparse.shape[0]*purchases_sparse.shape[1] # Number of possible interactions in the matrix
    num_purchases = len(purchases_sparse.nonzero()[0]) # Number of items interacted with
    sparsity = 100*(1 - (num_purchases/matrix_size))
    print(sparsity)
    
    return purchases_sparse

In [12]:
purchases_sparse = get_sparse_matrix(retail_data, (len(uid), len(pid)))
only_purchases_sparse = get_sparse_matrix(only_one_purchase, (len(uid), len(pid)))

91.96627463198068
97.1142612352987


In [45]:
POP = pd.read_csv('offer_pairs_PM_1009.csv')
MF = pd.read_csv('offer_pairs_MF_0609.csv')
GAT = pd.read_csv('offer_pairs.csv')

users = []
popr = []
mfr = []
gatr = []
for user in POP['0']:
    users.append(uidx[user])
    
    popr.append(pidx[int(POP[POP['0'] == user]['1'])])
    mfr.append(pidx[int(MF[MF['0'] == user]['1'])])
    gatr.append(pidx[int(GAT[GAT['0'] == user]['1'])])

recs = pd.DataFrame({'user_id': users, 'pop': popr, 'mf': mfr, 'gat': gatr})

In [76]:
cnt = 0
for ind, row in recs.iterrows():
    if row.pop != row.mf and row.mf != row.gat:
#         print(row)
        cnt += 1
print(cnt)

1933


In [54]:
# for i in purchases_sparse.toarray():
#     print(i)

In [55]:
retail_data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 145360 entries, 30 to 3306397
Data columns (total 5 columns):
 #   Column       Non-Null Count   Dtype  
---  ------       --------------   -----  
 0   date         145360 non-null  object 
 1   user_id      145360 non-null  int64  
 2   product_id   145360 non-null  int64  
 3   action_type  25035 non-null   float64
 4   Quantity     145360 non-null  float64
dtypes: float64(2), int64(2), object(1)
memory usage: 6.7+ MB


In [56]:
only_purchases_sparse

<3470x74 sparse matrix of type '<class 'numpy.float64'>'
	with 7410 stored elements in Compressed Sparse Row format>

In [57]:
import random

In [112]:
def make_train(ratings, purchases, pct_test = 0.2): # создает train и test
    '''
    This function will take in the original user-item matrix and "mask" a percentage of the original ratings where a
    user-item interaction has taken place for use as a test set. The test set will contain all of the original ratings, 
    while the training set replaces the specified percentage of them with a zero in the original ratings matrix. 
    
    parameters: 
    
    ratings - the original ratings matrix from which you want to generate a train/test set. Test is just a complete
    copy of the original set. This is in the form of a sparse csr_matrix. 
    
    pct_test - The percentage of user-item interactions where an interaction took place that you want to mask in the 
    training set for later comparison to the test set, which contains all of the original ratings. 
    
    returns:
    
    training_set - The altered version of the original data with a certain percentage of the user-item pairs 
    that originally had interaction set back to zero.
    
    test_set - A copy of the original ratings matrix, unaltered, so it can be used to see how the rank order 
    compares with the actual interactions.
    
    user_inds - From the randomly selected user-item indices, which user rows were altered in the training data.
    This will be necessary later when evaluating the performance via AUC.
    '''
    test_set = purchases.copy() # Make a copy of the original set to be the test set. 
#     test_set[test_set >= 1] = 1 # Store the test set as a binary preference matrix
#     test_set[test_set < 1] = 0
    
    training_set = ratings.copy() # Make a copy of the original data we can alter as our training set. 
    nonzero_inds = purchases.nonzero() # Find the indices in the ratings data where an interaction exists
    
#     print(type(training_set), training_set.shape)
#     nonzero_inds = [[], []]
#     for i in range(training_set.shape[0]):
#         for j in range(training_set.shape[1]):
#             if (training_set[i, j] >= 1):
#                 nonzero_inds[0].append(i)
#                 nonzero_inds[1].append(j)
#     nonzero_inds = pd.where(training_set >= 1)
    
    nonzero_pairs = list(zip(nonzero_inds[0], nonzero_inds[1])) # Zip these pairs together of user,item index into list
#     nonzero_pairs = [(i, j) for i, j in nonzero_pairs if training_set[i, j] >= 1]
    
    random.seed(0) # Set the random seed to zero for reproducibility
    num_samples = int(np.ceil(pct_test*len(nonzero_pairs))) # Round the number of samples needed to the nearest integer
    samples = random.sample(nonzero_pairs, num_samples) # Sample a random number of user-item pairs without replacement
    user_inds = [index[0] for index in samples] # Get the user row indices
    
    item_inds = [index[1] for index in samples] # Get the item column indices
    
#     removed_cnt = training_set[user_inds, item_inds].sum(axis=1)[0, 0]
#     total_cnt = ratings.sum(axis=0).sum(axis=1)[0, 0]
#     print(removed_cnt, total_cnt, removed_cnt / total_cnt)
    
#     training_set[user_inds, item_inds] = 0 # Assign all of the randomly chosen user-item pairs to zero
    for user, prod in samples:
        training_set[user, prod] = np.modf(training_set[user, prod])[0]

    user_purchases = [set() for i in range(ratings.shape[0])]
    print(len(set(nonzero_pairs)), len(set(nonzero_pairs).difference(set(samples))))
    for user, prod in set(nonzero_pairs).difference(set(samples)):
        user_purchases[user].add(prod)
        
    training_set.eliminate_zeros() # Get rid of zeros in sparse array storage after update to save space
    return training_set, test_set, list(set(user_inds)), user_purchases # Output the unique list of user rows that were altered  

In [113]:
product_train, product_test, product_users_altered, user_purchases = make_train(purchases_sparse, only_purchases_sparse, pct_test = 0.2)

7410 5928


In [114]:
import implicit

In [115]:
# обучение модели

alpha = 50

model = implicit.als.AlternatingLeastSquares(factors=10, regularization=100, iterations=22, use_gpu=False)
model.fit((product_train*alpha).T.astype('double'))

user_vecs = model.user_factors
item_vecs = model.item_factors

# print(model.rank_items(9, product_train*alpha, list(range(0, 6)), False))
# print(model.recommend(9, product_train*alpha, filter_already_liked_items=False))
# print(user_vecs[9].dot(item_vecs.T))
# print(purchases_sparse[9])

print(user_vecs.shape, item_vecs.shape)

  0%|          | 0/22 [00:00<?, ?it/s]

(3470, 10) (74, 10)


## Оценка точности

In [116]:
all_purchases = set(zip(only_one_purchase.user_id, only_one_purchase.product_id))

interesting_pairs = []
predicted_ratings = user_vecs.dot(item_vecs.T)

for user in product_users_altered:
    zero_inds = np.array(list(set(range(product_train.shape[1])).difference(user_purchases[user])))
#     training_row = product_test[user,:].toarray().reshape(-1) # Get the training set row
#     zero_inds = np.where(training_row < 0.01)[0]
    prod = zero_inds[np.argmax(predicted_ratings[user, zero_inds])]
    interesting_pairs.append((user, prod))

sum_cor = 0
for user, prod in interesting_pairs:
    if (user, prod) in all_purchases:
        sum_cor += 1
        
print(sum_cor)
print(len(interesting_pairs))

485
1301


# Генерация рекомендаций

In [125]:
# обучение модели

alpha = 50

model = implicit.als.AlternatingLeastSquares(factors=10, regularization=100, iterations=22, use_gpu=False)
model.fit((purchases_sparse*alpha).T.astype('double'))

user_vecs = model.user_factors
item_vecs = model.item_factors

# print(model.rank_items(9, product_train*alpha, list(range(0, 6)), False))
# print(model.recommend(9, product_train*alpha, filter_already_liked_items=False))
# print(user_vecs[9].dot(item_vecs.T))
# print(purchases_sparse[9])

print(user_vecs.shape, item_vecs.shape)



interesting_pairs = []
predicted_ratings = user_vecs.dot(item_vecs.T)

for user in range(purchases_sparse.shape[0]):
#     zero_inds = only_purchases_sparse[user].nonzero()
#     print(zero_inds)
#     zero_inds = np.array(list(set(range(purchases_sparse.shape[1])).difference(user_purchases[user])))
    training_row = product_test[user,:].toarray().reshape(-1) # Get the training set row
    zero_inds = np.where(training_row < 0.01)[0]
    prod = zero_inds[np.argmax(predicted_ratings[user, zero_inds])]
    interesting_pairs.append((user, prod))

offer_pairs_id = [(uid[user], pid[prod]) for user, prod in interesting_pairs]
pd.DataFrame(offer_pairs_id).to_csv('offer_pairs_MF_0609.csv')
# sum_cor = 0
# for user, prod in interesting_pairs:
#     if (user, prod) in all_purchases:
#         sum_cor += 1
        
# print(sum_cor)
# print(len(interesting_pairs))

  0%|          | 0/22 [00:00<?, ?it/s]

(3470, 10) (74, 10)


In [103]:
import heapq as hq
import tqdm

nz = only_purchases_sparse.nonzero()
set_purch = set(zip(nz[0], nz[1]))

max_cnt = 10000
cnt = 0
heap = []
for user in tqdm.tqdm(product_users_altered):
    ratings = user_vecs[user].dot(item_vecs.T)
    training_row = product_train[user].toarray().reshape(-1)
    zero_inds = np.where(training_row < 0.01)
    for prod in zero_inds[0]:
        cnt += 1
        hq.heappush(heap, (ratings[prod], user, prod))
        if cnt > max_cnt:
            hq.heappop(heap)
            
heap = sorted(heap, reverse=True)

100%|████████████████████████████████████████████████████████████████████████████| 1301/1301 [00:00<00:00, 2001.52it/s]


In [75]:
# for rate, u, p in heap:
#     if product_train[u, p] > 0:
#         print(u, p)
# (3144, 1) in all_purch
# # purchases_sparse[3144, 1]
# # training_row = product_train[3144].toarray().reshape(-1)
# # zero_inds = np.where(training_row < 0.01)
# # training_row

In [76]:
user_vecs[919].dot(item_vecs[6].T)

0.27693757

In [77]:
all_purch = set(zip(only_one_purchase.user_id, only_one_purchase.product_id))
sum_cor = 0
for rate, user, prod in heap:
    if (user, prod) in all_purch:
        sum_cor += 1
    else:
        pass
#         print(user, prod, rate, purchases_sparse[user, prod])
print(sum_cor)

1069


In [78]:
len(all_purch)

7410

In [79]:
ratings = user_vecs[product_users_altered[0]].dot(item_vecs.T)


len(np.where(training_row < 0.01)[0])

71

In [80]:
from sklearn import metrics

def auc_score(predictions, test):
    '''
    This simple function will output the area under the curve using sklearn's metrics. 
    
    parameters:
    
    - predictions: your prediction output
    
    - test: the actual target result you are comparing to
    
    returns:
    
    - AUC (area under the Receiver Operating Characterisic curve)
    '''
    fpr, tpr, thresholds = metrics.roc_curve(test, predictions)
#     metrics.RocCurveDisplay(fpr, tpr).plot()
    return metrics.auc(fpr, tpr)   

In [81]:
def calc_mean_auc(training_set, altered_users, predictions, test_set):
    '''
    This function will calculate the mean AUC by user for any user that had their user-item matrix altered. 
    
    parameters:
    
    training_set - The training set resulting from make_train, where a certain percentage of the original
    user/item interactions are reset to zero to hide them from the model 
    
    predictions - The matrix of your predicted ratings for each user/item pair as output from the implicit MF.
    These should be stored in a list, with user vectors as item zero and item vectors as item one. 
    
    altered_users - The indices of the users where at least one user/item pair was altered from make_train function
    
    test_set - The test set constucted earlier from make_train function
    
    
    
    returns:
    
    The mean AUC (area under the Receiver Operator Characteristic curve) of the test set only on user-item interactions
    there were originally zero to test ranking ability in addition to the most popular items as a benchmark.
    '''
    
    
    store_auc = [] # An empty list to store the AUC for each user that had an item removed from the training set
    popularity_auc = [] # To store popular AUC scores
    pop_items = np.array(test_set.sum(axis = 0)).reshape(-1) # Get sum of item iteractions to find most popular
    item_vecs = predictions[1]
    for user in altered_users: # Iterate through each user that had an item altered
        training_row = training_set[user,:].toarray().reshape(-1) # Get the training set row
        zero_inds = np.where(training_row < 0.01) # Find where the interaction had not yet occurred
#         print(training_row)
        # Get the predicted values based on our user/item vectors
        user_vec = predictions[0][user,:]
        pred = user_vec.dot(item_vecs).toarray()[0,zero_inds].reshape(-1)
        # Get only the items that were originally zero
        # Select all ratings from the MF prediction for this user that originally had no iteraction
        actual = test_set[user,:].toarray()[0,zero_inds].reshape(-1)
        
        # Select the binarized yes/no interaction pairs from the original full data
        # that align with the same pairs in training 
        pop = pop_items[zero_inds] # Get the item popularity for our chosen items
#         print(actual)
#         print(user, pred)
#         print(pop)
        store_auc.append(auc_score(pred, actual)) # Calculate AUC for the given user and store
        popularity_auc.append(auc_score(pop, actual)) # Calculate AUC using most popular and score
    # End users iteration
    

    return float('%.3f'%np.mean(store_auc)), float('%.3f'%np.mean(popularity_auc))
#     return float('%.3f'%np.mean(store_auc))
   # Return the mean AUC rounded to three decimal places for both test and popularity benchmark

In [82]:
calc_mean_auc(product_train, product_users_altered, 
              [sparse.csr_matrix(user_vecs), sparse.csr_matrix(item_vecs.T)], product_test)
# AUC for our recommender system

(0.932, 0.939)

## Перебор параметров

In [42]:
def print_log(row, header=False, spacing=12):
    top = ''
    middle = ''
    bottom = ''
    for r in row:
        top += '+{}'.format('-'*spacing)
        if isinstance(r, str):
            middle += '| {0:^{1}} '.format(r, spacing-2)
        elif isinstance(r, int):
            middle += '| {0:^{1}} '.format(r, spacing-2)
        elif isinstance(r, float):
            middle += '| {0:^{1}.5f} '.format(r, spacing-2)
        bottom += '+{}'.format('='*spacing)
    top += '+'
    middle += '|'
    bottom += '+'
    if header:
        print(top)
        print(middle)
        print(bottom)
    else:
        print(middle)
        print(top)

In [43]:
def learning_curve(altered_users, predictions, model, train, test, epochs, k=5, user_index=None):
    if not user_index:
        user_index = range(train.shape[0])
    prev_epoch = 0
    # train_precision = []
    # train_mse = []
    # test_precision = []
    # test_mse = []
    test_auc = []
    
    headers = ['epochs', 'auc']
    print_log(headers, header=True)
    
    for epoch in epochs:
        model.iterations = epoch - prev_epoch
        if not hasattr(model, 'user_vectors'):
            model.fit(train.T)
        else:
            model.fit_partial(train.T)
        
        test_auc.append(calc_mean_auc(train, 
                                      altered_users, 
                                      [sparse.csr_matrix(model.user_factors), sparse.csr_matrix(model.item_factors.T)], 
                                      test)[0])
        # train_mse.append(calculate_mse(model, train, user_index))
        # train_precision.append(precision_at_k(model, train, k, user_index))
        # test_mse.append(calculate_mse(model, test, user_index))
        # test_precision.append(precision_at_k(model, test, k, user_index))
        # row = [epoch, train_precision[-1], test_precision[-1],
        #        train_mse[-1], test_mse[-1]]
        row = [epoch, test_auc[-1]]
        print_log(row)
        prev_epoch = epoch
    # return model, train_precision, train_mse, test_precision, test_mse
    return model, test_auc

In [44]:
import itertools
import copy

def grid_search_learning_curve(altered_users, predictions, base_model, train, test, param_grid,
                               user_index=None, patk=5, epochs=range(2, 40, 5)):
    """
    "Inspired" (stolen) from sklearn gridsearch
    https://github.com/scikit-learn/scikit-learn/blob/master/sklearn/model_selection/_search.py
    """
    curves = []
    keys, values = zip(*param_grid.items())
    for v in itertools.product(*values):
        params = dict(zip(keys, v))
        this_model = copy.deepcopy(base_model)
        print_line = []
        for k, v in params.items():
            if k == 'alpha':
                train = train * v
            else:
                setattr(this_model, k, v)
            print_line.append((k, v))

        print(' | '.join('{}: {}'.format(k, v) for (k, v) in print_line))
        # _, train_patk, train_mse, test_patk, test_mse = learning_curve(this_model, train, test,
        #                                                         epochs, k=patk, user_index=user_index)
        _, test_auc = learning_curve(altered_users, predictions, this_model, train, test, epochs, k=patk, user_index=user_index)

        # curves.append({'params': params,
        #                'patk': {'train': train_patk, 'test': test_patk},
        #                'mse': {'train': train_mse, 'test': test_mse}})
        curves.append({'params': params,
                       'auc': {'test': test_auc}})
        train = train / params['alpha']
    return curves

In [45]:
param_grid = {'num_factors': [10, 20, 40],
              'regularization': [1e2],
              'alpha': [10, 50, 100]}

# param_grid = {'num_factors': [2, 5, 10, 20, 40],
#               'regularization': [0.0, 1e-5, 1e-3, 1e-1, 1e1, 1e2],
#               'alpha': [1, 10, 50, 100, 500, 1000]}

# param_grid = {'num_factors': [2, 5, 10, 20, 40],
#               'regularization': [0.0, 1e-5, 1e-3, 1e-1, 1e1, 1e2]}

In [46]:
base_model = implicit.als.AlternatingLeastSquares(use_gpu=False)

In [47]:
 curves = grid_search_learning_curve(product_users_altered, 
              [sparse.csr_matrix(user_vecs), sparse.csr_matrix(item_vecs.T)], 
              base_model, product_train, product_test,
                                    param_grid,
                                    patk=5)

num_factors: 10 | regularization: 100.0 | alpha: 10
+------------+------------+
|   epochs   |    auc     |
+============+============+


  0%|          | 0/2 [00:00<?, ?it/s]

|     2      |  0.78500   |
+------------+------------+


  0%|          | 0/5 [00:00<?, ?it/s]

|     7      |  0.77800   |
+------------+------------+


...

|     12     |  0.78400   |
+------------+------------+


  0%|          | 0/5 [00:00<?, ?it/s]

|     17     |  0.78400   |
+------------+------------+


  0%|          | 0/5 [00:00<?, ?it/s]

KeyboardInterrupt: 

In [38]:
best_curves = sorted(curves, key=lambda x: max(x['auc']['test']), reverse=True)

print(best_curves[0]['params'])
max_score = max(best_curves[0]['auc']['test'])
print(max_score)
iterations = range(2, 40, 2)[best_curves[0]['auc']['test'].index(max_score)]
print('Epoch: {}'.format(iterations))

{'num_factors': 10, 'regularization': 100.0, 'alpha': 50}
0.978
Epoch: 10


## Топ 10000 популярных пар

In [323]:
import heapq as hq

nz = only_purchases_sparse.nonzero()
set_purch = set(zip(nz[0], nz[1]))

max_cnt = 10000
cnt = 0
matrix = user_vecs.dot(item_vecs.T)
heap = []
for i in range(matrix.shape[0]):
    for j in range(matrix.shape[1]):
        if (i, j) not in set_purch:
            cnt += 1
            hq.heappush(heap, (matrix[i, j], uid[i], pid[j]))
            if cnt > max_cnt:
                hq.heappop(heap)
heap

[(0.71594876, '6514f322aafacd9ab94f31b8e6cb0768dfe87ab2', 192),
 (0.7159536, '9aa8dde73001852e84cbb48b53131432b2496519', 192),
 (0.7160886, 'dc16d82dd4469f9b18748fee6ecc5a00791f4bec', 44),
 (0.71595615, 'f438807f6cf7d88c19e50ddbf8120cac2423bbe8', 35),
 (0.71600217, '47fdc059e1d563dd7bbac605187229fb697ece01', 1144),
 (0.71617067, 'd178a0ef344512fbf65625bcc58fd2dc6568eb61', 44),
 (0.71608937, 'b78613f476501552b2b497c6a248ea9af72c2b41', 527),
 (0.7159875, 'c740798d125a543bbe9ad0c5ecd35ad104a00458', 1144),
 (0.71601915, 'ed9e08fdc0d66f21e4de05b8a7d1eda64a024707', 192),
 (0.7161004, '778c006af13b1f7ee12c4be87533139dd5e84a06', 575),
 (0.71605563, 'ae8c3d9861340d07186989c94518003f5ed1859a', 176),
 (0.7161988, 'cc7e63e8eadb72009522e400b6bc66f02975561d', 527),
 (0.7162851, 'db1bce0d9dfdcd66aeacfc5632e9174350eed98b', 192),
 (0.7161912, 'faafeb94a3fc29667d8843c6f843b5036db4b948', 527),
 (0.7162511, 'bbfcdc52657db4540c53cc192e789318dc35e49a', 44),
 (0.71609926, '90ba93ae223603f521b126cf272a6954a1d

In [294]:
heap = sorted(heap, reverse=True)
usid = [i[1] for i in heap]
prid = [i[2] for i in heap]
usid

['...',
 ...]

In [295]:
df = pd.DataFrame({'user_id': usid, 'product_id': prid})
df.to_csv('top10000.csv')

In [296]:
df = pd.read_csv('top10000.csv')
df.shape

(10000, 3)